### Importation des bibliothèques, fonctions, algorithmes nécessaires pour ce notebook

In [64]:
import pandas as pd
import numpy as np
import seaborn as sns
sns.set_theme()
import matplotlib.pyplot as plt
%matplotlib inline

from time import time, sleep
from dateutil.relativedelta import relativedelta

from IPython.display import Audio
import librosa
import librosa.display
from scipy import signal

import catboost
from catboost import CatBoostClassifier
import lightgbm
from lightgbm import LGBMClassifier
import xgboost
from xgboost import XGBClassifier

from sklearn.experimental import enable_hist_gradient_boosting
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split, StratifiedKFold, cross_val_score
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier 
from sklearn.ensemble import (RandomForestClassifier, AdaBoostClassifier, BaggingClassifier,
                              GradientBoostingClassifier, ExtraTreesClassifier, HistGradientBoostingClassifier)

from sklearn.tree import DecisionTreeClassifier

from random import sample

### Chargement de la base contenant les liens vers les morceaux rééchantillonnés à 22050Hz 

In [65]:
df = pd.read_csv ('DSD100_paths22050.csv', index_col=0)
df

Name                      Style  \
Id                                                                    
1                      ANiMAL - Clinic A                 UK Hip-Hop   
2                      ANiMAL - Rockshow                 UK Hip-Hop   
3             Actions - One Minute Smile                  Power Pop   
4        Al James - Schoolboy Facination              Bubblegum Pop   
5    Angela Thomas Wade - Milk Cow Blues                    Country   
..                                   ...                        ...   
96                  Triviul - Angelsaint  Leftfield Pop/Electronica   
97       Triviul feat. The Fiend - Widow              Urban R&B/Pop   
98                 Wall Of Death - Femme                Black Metal   
99          Young Griffo - Blood To Bone        Anthemic Heavy Rock   
100               Young Griffo - Pennies        Anthemic Heavy Rock   

                                                   mix  \
Id                                                       
1    /Users/francoistouchard/Music/DSD100/22050torc...   
2    /Users/francoistouchard/Music/DSD100/22050torc...   
3    /Users/francoistouchard/Music/DSD100/22050torc...   
4    /Users/francoistouchard/Music/DSD100/22050torc...   
5    /Users/francoistouchard/Music/DSD100/22050torc...   
..                                                 ...   
96   /Users/francoistouchard/Music/DSD100/22050torc...   
97   /Users/francoistouchard/Music/DSD100/22050torc...   
98   /Users/francoistouchard/Music/DSD100/22050torc...   
99   /Users/francoistouchard/Music/DSD100/22050torc...   
100  /Users/francoistouchard/Music/DSD100/22050torc...   

                                                vocals  \
Id                                                       
1    /Users/francoistouchard/Music/DSD100/22050torc...   
2    /Users/francoistouchard/Music/DSD100/22050torc...   
3    /Users/francoistouchard/Music/DSD100/22050torc...   
4    /Users/francoistouchard/Music/DSD100/22050torc...   
5    /Users/francoistouchard/Music/DSD100/22050torc...   
..                                                 ...   
96   /Users/francoistouchard/Music/DSD100/22050torc...   
97   /Users/francoistouchard/Music/DSD100/22050torc...   
98   /Users/francoistouchard/Music/DSD100/22050torc...   
99   /Users/francoistouchard/Music/DSD100/22050torc...   
100  /Users/francoistouchard/Music/DSD100/22050torc...   

                                                 music  
Id                                                      
1    /Users/francoistouchard/Music/DSD100/22050torc...  
2    /Users/francoistouchard/Music/DSD100/22050torc...  
3    /Users/francoistouchard/Music/DSD100/22050torc...  
4    /Users/francoistouchard/Music/DSD100/22050torc...  
5    /Users/francoistouchard/Music/DSD100/22050torc...  
..                                                 ...  
96   /Users/francoistouchard/Music/DSD100/22050torc...  
97   /Users/francoistouchard/Music/DSD100/22050torc...  
98   /Users/francoistouchard/Music/DSD100/22050torc...  
99   /Users/francoistouchard/Music/DSD100/22050torc...  
100  /Users/francoistouchard/Music/DSD100/22050torc...  

[100 rows x 5 columns]

### Petite écoute aléatoire 

In [66]:
n = sample (range(100),1)
    
source = sample (['mix', 'vocals', 'music'], 1)
    
audio , __ = librosa.load (df.loc[n[0],source[0]], sr=None)
    
print ('Morceau n°{}, canal {}'.format (n[0], source[0]))

Audio (audio, rate = 22050)

Morceau n°18, canal mix


### Création des fonctions pour générer data et target

In [67]:
sc = MinMaxScaler()

def audio (stem):
    
    audio , __ = librosa.load (stem, sr=None)
    
    return audio
    

def Z (y, fe = 22050, n_fft = 1024, hop_length = 256):
    
    f,t,S = signal.stft (y, fs=fe , nperseg=n_fft, noverlap=n_fft-hop_length)
    
    S = np.abs(S)
    S = np.rot90 (S, 1)
    S = sc.fit_transform(S)
    S = np.rot90 (S, 3)

    return S


#Découpage d'un morceau en fenètres de largeur = 25, se décalant d'une unité à chaque itération.

def DATAset (n, fonction=Z, seuil=0, red_temp=5):
    
    X = fonction (audio(df.loc[n,'mix']))
    X = X[ : , : X.shape[1]//red_temp]        # on choisit la réduction temporelle du signal
    s = X.shape[1]                             
    Y = fonction (audio(df.loc[n,'vocals']))   # seuil nul par défaut
    Y = Y[ :128 , : s]
    Σ = np.sum (Y, axis = 0)    #Somme sur les 128 premiers pas de fréquence
    y = np.where (Σ > seuil, 1, 0) #Si la somme est >seuil y prend 1 sinon 0
    y = y.reshape (-1,)
    
    data = []
    target = []
    
    for i in range (s-24):
        x = X[ : , 0+i:25+i] #matrices de 25 pas de temps du signal mix se décalant d'un pas 
        x = x.reshape (1,-1) #remise en forme vecteur pour les algorithmes de classification testés
        data.append (x)
        target.append(y[12+i]) #la cible est prise au milieu de la fenêtre de 25 pas temporels
        
    return data, target

### Selection par style musical des morceaux retenus pour l'entrainement

In [68]:
print ("La base complète est constituée de", len(np.unique(df['Style'][~df['Style'].isna()].astype(str))) , "styles différents\
 pour 100 morceaux")

La base complète est constituée de 65 styles différents pour 100 morceaux


In [69]:
np.unique(df['Style'][~df['Style'].isna()].astype(str), return_index=True)

(array(['Acoustic Indie Pop', 'Acoustic Singer-Songwriter', 'Alt Pop/Rock',
        'Alternative Electro Rock', 'Alternative Punk-Rock',
        'Alternative Rock Ballad', 'Americana', 'Anthemic Heavy Rock',
        'Atmospheric Electronic Pop', 'Atmospheric Indie Pop',
        'Basque Indie Rock', 'Black Metal', 'Bollywood', 'Bubblegum Pop',
        'Buckley-esque Indie Rock', 'Classic Heavy Rock',
        'Classic Psychedelic Rock', 'Club Rock', 'Country', 'Country Rock',
        'Dark Break-based Dance', 'Death Metal', 'Drum & Bass',
        'Electronic Dance Pop', 'Electronic Rock/Pop',
        'Electronica/Classical Crossover', 'Emo Rock', 'Epic Indie Rock',
        'Funk Rock', 'Gothic Electro', 'Heavy Metal',
        'High-Energy Heavy Rock', 'Hip-Hop', 'Indie Funk/Rock',
        'Indie Pop', 'Indie Pop/Rock', 'Indie Rock',
        'Indie Singer-Songwriter', 'Intimate Pop Ballad',
        'Irish-Language Singer-Songwriter', 'Jazz/Singer-Songwriter',
        'Laid-back Blues-Rock

In [70]:
__ , index = np.unique(df['Style'][~df['Style'].isna()].astype(str), return_index=True)

In [71]:
train = list(index+1)

print(train), len(train)

[42, 20, 82, 79, 16, 29, 34, 49, 37, 24, 60, 93, 33, 4, 66, 22, 8, 74, 5, 39, 61, 11, 36, 51, 32, 68, 80, 50, 26, 17, 12, 48, 76, 31, 19, 9, 28, 88, 72, 64, 30, 47, 13, 77, 27, 45, 14, 58, 59, 67, 3, 81, 91, 7, 35, 56, 43, 55, 1, 92, 63, 23, 96, 84, 6]


(None, 65)

In [72]:
test = sample([x for x in range (1,101) if x not in train],16)

print(test)

[44, 2, 62, 41, 40, 94, 86, 75, 71, 90, 98, 25, 78, 70, 100, 97]


In [73]:
len(np.unique(train+test))

81

# Constitution de la base TRAIN

In [74]:
seuil=0
red_temp=5

d = time()

X_train, y_train = DATAset (train[0], fonction = Z, seuil=seuil, red_temp=red_temp)

for i in range (1,len(train)):
    
    X,Y = DATAset (train[i], fonction = Z, seuil=seuil, red_temp=red_temp)
    X_train.extend(X)
    y_train.extend(Y)

X_train = np.array (X_train).reshape(-1,25*513)
y_train = np.array (y_train, dtype=int)


f = time()
relativedelta (seconds=f-d)

relativedelta(seconds=+42.0291)

In [75]:
X_train.shape ,y_train.shape

#La réduction temporelle de 5 conduit à environ 300 000 entrées de 12825 features

((287285, 12825), (287285,))

# Constitution de la base TEST

In [76]:
d = time()

X_test, y_test = DATAset (test[0], fonction = Z, seuil=seuil, red_temp=red_temp)

for i in range (1,len(test)):
    x,Y = DATAset (test[i], fonction = Z, seuil=seuil, red_temp=red_temp)
    X_test.extend(x)
    y_test.extend(Y)

X_test = np.array(X_test).reshape(-1,25*513)
y_test = np.array (y_test) 

f = time()
relativedelta (seconds=f-d)

relativedelta(seconds=+7.41469)

In [77]:
X_test.shape, y_test.shape

((66086, 12825), (66086,))

# Cross-val score pour comparaison de divers algorithmes 

In [15]:
pca = PCA (0.91)

X_train_pca = pca.fit_transform (X_train)

print ('La PCA(0.91) a permis de faire passer le nombre de features de',25*513,'à', pca.n_components_)

# Division par 4 environ du nombre de features du fait de la pca. C'est tout de même conséquent.

La PCA(0.91) a permis de faire passer le nombre de features de 12825 à 3042


In [29]:
DTC = DecisionTreeClassifier (max_depth=6) #limitation à 6 de la profondeur des arbres pour éviter l'overfitting

RF = RandomForestClassifier (n_estimators = 500) #paramètres par défaut à part l'augmentation du nombre 
#des estimators

ETC = ExtraTreesClassifier (n_estimators = 500) #paramètres par défaut à part l'augmentation du nombre
#des estimators

AdaB = AdaBoostClassifier (base_estimator = DTC, n_estimators = 500) #utilisation de "l'abre de décision" défini
#ci-avant et estimators à 500

BC = BaggingClassifier (n_estimators = 500, oob_score = True) #paramètres par défaut à part l'augmentation
#du nombre des estimators et oob_score=True

HGB = HistGradientBoostingClassifier (max_iter = 5000) #paramètres par défaut à part l'augmentation du nombre
#d'itérations

CB = CatBoostClassifier (iterations=1000) #paramètres par défaut à part l'augmentation du nombre
#d'itérations

#XGB = XGBClassifier () #N'a pu être utilisé. Le kernel explose dès le lancement de la cellule.
#Le passade du format np.array aux matrices xgboost n'est pas gérable sur cette quantité de données

LGBM = LGBMClassifier (objective='binary', n_estimators = 500) #paramètres par défaut à part l'augmentation
#du nombre des estimators

GBC = GradientBoostingClassifier (max_depth = 6, n_estimators = 500) #paramètres par défaut à part l'augmentation
#du nombre des estimators. Profondeur choisie à 6 pour être la même que DTC et CatBoost

LR = LogisticRegression (max_iter = 10000) #augmentation du nombre possible d'itérations pour
#assurer la convergence

SVM = SVC()

KNN = KNeighborsClassifier ()


scores={} #Dictionnaire pour stocker les résultats du cross val score

duration={} #Dictionnaire pour stocker les durées de process pour chaque algorithme

KFold = StratifiedKFold (shuffle=True) #KFold externe par défaut à 5 splits (équivalent à un 80/20)

In [ ]:
for clé, model in zip (['DTC','RF', 'ETC', 'AdaB', 'BC', 'HGB', 'CB', 'LGBM', 'GBC', 'LR', 'SVM', 'KNN'],
[DTC, RF, ETC, AdaB, BC, HGB, CB, LGBM, GBC, LR, SVM, KNN]):                                                                             

    d=time()

    scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)
    
    f=time()
    
    duration[clé] = f-d

    print (f'{clé} Accuracy moyenne : {np.mean(scores[clé]):.1%}, durée : {duraction[clé]} \n')

Results = pd.DataFrame(scores).describe().round(4).loc[['mean', 'std', 'min', 'max']]

Results.loc['duration'] = [duration[clé] for clé in ['DTC','RF', 'ETC', 'AdaB', 'BC', 'HGB', 'CB', 'LGBM', 'GBC', 'LR', 'SVM', 'KNN']]

In [30]:
d=time()

clé = 'DTC'
model = DTC

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 75.5%


relativedelta(minutes=+7, seconds=+45.2655)

In [24]:
d=time()

clé = 'RF'
model = RF

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 88.5%


relativedelta(hours=+2, minutes=+2, seconds=+44.0168)

In [23]:
d=time()

clé = 'ETC'
model = ETC

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 78.5%


relativedelta(minutes=+33, seconds=+37.9209)

In [19]:
d=time()

clé = 'AdaB'
model = AdaB

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 97.8%


relativedelta(days=+2, hours=+18, minutes=+38, seconds=+1.31622)

In [25]:
d=time()

clé = 'BC'
model = BC

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)

Accuracy moyenne : 97.7%


relativedelta(days=+4, hours=+14, minutes=+36, seconds=+54.9004)

In [28]:
d=time()

clé = 'HGB'
model = HGB

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 99.2%


relativedelta(hours=+1, minutes=+39, seconds=+52.2243)

In [32]:
d=time()

clé = 'CB'
model = CB

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 96.9%


relativedelta(minutes=+21, seconds=+34.7676)

In [20]:
d=time()

clé = 'LGBM'
model = LGBM

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 96.7%


relativedelta(minutes=+19, seconds=+32.3609)

In [31]:
GBC = GradientBoostingClassifier (max_depth = 6, n_estimators = 500)
d=time()

clé = 'GBC'
model = GBC

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 97.2%


relativedelta(days=+2, hours=+14, seconds=+24.5397)

In [32]:
d=time()

clé = 'LR'
model = LR

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 82.8%


relativedelta(minutes=+4, seconds=+19.9739)

In [34]:
d=time()

clé = 'SVM'
model = SVM

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 94.6%


relativedelta(hours=+23, minutes=+21, seconds=+20.0756)

In [33]:
d=time()

clé = 'KNN'
model = KNN

scores[clé] = cross_val_score (model, X_train_pca, y_train, cv=KFold, n_jobs=-1)

f=time() 

print (f'Accuracy moyenne : {np.mean(scores[clé]):.1%}')

relativedelta (seconds=f-d)   

Accuracy moyenne : 96.2%


relativedelta(hours=+1, minutes=+4, seconds=+0.763536)